# TM09 Topic Modeling by BERtopic

![Alt text](img/img_tm09_1.png)

## Process comparison

* 原始的群集法需要先把文檔處理成近似「Document-Term Matrix」的型態（雖然現在skilearn都可以代勞）。在這之前會需要做好幾個步驟的資料清理，包含去除一些數字或英文字母、移除空白、斷詞、移除停用詞、留下保留字等。
* 若是用Embedding則不需要先移除停用詞，因為停用詞也可能是其他詞的「脈絡」，若把停用詞都移掉了，可能會喪失一些脈絡，因此，使用Embedding的話，先不用移除停用詞，也不見得需要做TF-IDF的重要關鍵字萃取。
* 如果是用SimpleTransformer與BERTopic這類深度學習架構，因為模型中包含將文檔轉換為文檔向量的過程，所以不用特地做資料清理或抽取關鍵字，都是在最後一個階段的群集結果呈現時，才需要對文檔做斷詞以便於呈現。


![Alt text](img/img_tm09_2.png)

In [36]:
from IPython.display import display
pd.options.display.float_format = '{:.4f}'.format

import warnings
warnings.filterwarnings("ignore", message=".*The 'nopython' keyword.*")
# import os
# os.environ["TOKENIZERS_PARALLELISM"] = "false"

import re
import zhon.hanzi
from collections import Counter
zh_pat = f"[{zhon.hanzi.characters}|{zhon.hanzi.punctuation}]"

with open("data/stopwords_zh-tw.txt", encoding="utf-8") as fin:
    stopwords = fin.read().split("\n")[1:]

## Step 1. Import and clean data

Notes that we don't need tokenization and stop-word removal here. Just clean up space or punctuation. 

In [5]:
import pandas as pd
df = pd.read_csv('data/sentiment.csv')

def clean_text(text):
    text = re.sub("[\r\t ]+", " ", text)
    text = "".join(re.findall(zh_pat, text))
    return text

df["cleaned"] = df["text"].apply(clean_text)

## Step 2 Run BERTopic

### 2.1 Prepare envs for bertopic

In [10]:
df.cleaned

0                        店家很給力，快遞也是相當快，第三次光顧啦
1       這樣的配置用系統還是有點卡。指紋收集器。沒送原裝滑鼠還需要自己買，不太好。
2                        不錯，在同等檔次酒店中應該是值得推薦的！
3                             哎！不會是蒙牛乾的吧嚴懲真凶！
4                 空尤其是三立電視臺女主播做的序尤其無趣像是硬湊那麼多字
                        ...                  
6383                      價效比高、記憶體大、功能全，螢幕超清晰
6384                你太狠了…告訴你他們不會喧譁的人，肯定是蒙牛喝多了
6385                 醫生居然買了蒙牛，我是喝呢還是不喝呢還是不喝呢？
6386                     我只想說夾蒙牛是不對的販賣毒品是犯罪行為
6387                                     蒙牛便宜
Name: cleaned, Length: 6388, dtype: object

### 2.1 Initialize model

In [11]:
# !pip install bertopic
# !pip install hdbscan
# !pip install jieba

from bertopic import BERTopic
from transformers.pipelines import pipeline

from bertopic.vectorizers import ClassTfidfTransformer
from bertopic.representation import KeyBERTInspired
from sklearn.feature_extraction.text import CountVectorizer

import jieba
jieba.load_userdict("data/userdict.txt") # prepared by yourself

from hdbscan import HDBSCAN

def tokenize_zh(text):
   words = jieba.lcut(text)
   return words


# embedding_model = pipeline("feature-extraction", model="ckiplab/bert-base-chinese")
# embeddings = [embedding_model(doc)[0] for doc in docs] # Asking chatGPT but wrong
# embeddings = embedding_model.encode(docs, show_progress_bar=False) # by BERTopic's sentence transformer


vectorizer_model = CountVectorizer(tokenizer=tokenize_zh, stop_words=stopwords)
ctfidf_model = ClassTfidfTransformer(reduce_frequent_words=True)
representation_model = KeyBERTInspired()
hdbscan_model = HDBSCAN(min_cluster_size = 20, metric='euclidean',
                        cluster_selection_method='eom', prediction_data=True, min_samples=10)


docs = df["cleaned"]
print(len(docs))

6388


Batches: 100%|██████████| 200/200 [00:27<00:00,  7.26it/s]
2023-12-03 00:52:55,997 - BERTopic - Transformed documents to Embeddings
2023-12-03 00:53:06,965 - BERTopic - Reduced dimensionality
2023-12-03 00:53:08,310 - BERTopic - Clustered reduced embeddings


### 2.2 Run bertopic

In [37]:
"""
There are a few parameters that you can tune to improve your topic model.
Here I provides some examples:
Model 1: Default parameters
Model 2: Specify the language and embedding model
Model 3: Specify more parameters
"""

# Model 1
# topic_model = BERTopic()

# Model 2
# topic_model = BERTopic(
#     language="chinese (traditional)",
#     embedding_model="distiluse-base-multilingual-cased-v1",
#     calculate_probabilities=True, verbose=True)

# Model 3
topic_model = BERTopic(
    language="chinese (traditional)",
    #    embedding_model="paraphrase-xlm-r-multilingual-v1",
    embedding_model="distiluse-base-multilingual-cased-v1",
    vectorizer_model=vectorizer_model,
    #    representation_model=representation_model,
    #    ctfidf_model=ctfidf_model,
    calculate_probabilities=True, verbose=True)
topics, probs = topic_model.fit_transform(docs)

Batches: 100%|██████████| 200/200 [00:32<00:00,  6.07it/s]
2023-12-03 12:04:38,881 - BERTopic - Transformed documents to Embeddings
2023-12-03 12:04:43,698 - BERTopic - Reduced dimensionality
2023-12-03 12:04:44,907 - BERTopic - Clustered reduced embeddings


## Step 3. Result exploration

### Terms probability of each topic

In [12]:
topic_model.get_topic(0)

[('酒店', 0.03997580428200383),
 ('房間', 0.038745198337690454),
 ('住', 0.022947505352807967),
 ('服務', 0.021592129521251717),
 ('環境', 0.02153355858267068),
 ('早餐', 0.020479389742980674),
 ('設施', 0.020377022207918306),
 ('入住', 0.017575327768934505),
 ('方便', 0.015658263760673603),
 ('交通', 0.015161822535778819)]

### Topic counts and representative docs

In [26]:
freq = topic_model.get_topic_info();
freq.head(16)

Topic  Count              Name                             Representation  \
0      -1   2010       -1_蒙牛_ _買_喝         [蒙牛,  , 買, 喝, 不錯, 書, 外觀, 好, 支援, 說]   
1       0    842      0_酒店_房間_住_服務    [酒店, 房間, 住, 服務, 環境, 早餐, 設施, 入住, 方便, 交通]   
2       1    160    1_電池_小時_電池續_耐用  [電池, 小時, 電池續, 耐用, 機時間, 時間, 航時間, 短, 能力, 長]   
3       2    148     2_鍵盤_手感_舒服_按鍵      [鍵盤, 手感, 舒服, 按鍵, 鍵, 螢幕, 好, 價效, 外觀, 盤]   
4       3    133     3_鈴聲_聲音_效果_音質    [鈴聲, 聲音, 效果, 音質, 功能, 聽, 螢幕, 音量, 顯示, 拍照]   
5       4    119      4_內容_說_失望_優點     [內容, 說, 失望, 優點, 覺得, 人, 感覺, 暢銷, 宣傳, 好看]   
6       5    119      5_螢幕_屏_顯示_完美    [螢幕, 屏, 顯示, 完美, 亮點, 效果, 外觀, 功能, 色彩, 配置]   
7       6    118       6_蒙牛_逼_牛_抵制        [蒙牛, 逼, 牛, 抵制, 真, 悲劇, 傻, 可怕,  , 垃圾]   
8       7     98       7_收到_月_日_訂單      [收到, 月, 日, 訂單, 還沒, 書, 噹噹, 通知, 缺貨, 沒貨]   
9       8     98  8_安裝_師傅_還沒安裝_安裝費  [安裝, 師傅, 還沒安裝, 安裝費, 東西, 再, 好, 正品, 先給, 好評]   
10      9     87      9_光碟_硬碟_分割_槽     [光碟, 硬碟, 分割, 槽, 機, 外接, 系統, 燒錄, 麻煩, 驅動]   
11     10     85    10_這本書_書_一本_作者    [這本書, 書, 一本, 作者, 寫, 內容, 沒什麼, 完, 炒作, 文筆]   
12     11     85   11_系統_預裝_裝系統_安裝    [系統, 預裝, 裝系統, 安裝, 麻煩, 弄, 作業, 軟體, 裝, 解除]   
13     12     84    12_酸奶_牛奶_紅棗_喜歡  [酸奶, 牛奶, 紅棗, 喜歡, 好喝, 酸牛奶, 蒙牛, 喝, 酸酸乳, 味道]   
14     13     77    13_簡訊_電話_訊號_通話     [簡訊, 電話, 訊號, 通話, 關機, 訊, 彩信, 容量, 不好, 短]   
15     14     77     14_記憶體_加_跑_體條    [記憶體, 加, 跑, 體條, 太小, 記憶, 升級, 插槽, 系統, 速度]   

                                  Representative_Docs  
0                           [喜歡喝蒙牛不？, 為何沒有蒙牛？, 蒙牛好！！]  
1   [環境很好，服務也不錯，推薦下次還會住這裡, 酒店位置很好，房間也很舒服，下次還會入住。, ...  
2   [電池待機時間長，機身小巧，功能比較實用, 電池待機時間長，機身小巧時尚, 外觀漂亮，電池很...  
3   [散熱好，螢幕清晰，鍵盤手感很好，處理速度快，硬碟聲音小，做工不錯, 價效比好。鍵盤手感挺好...  
4   [聲音好聽，外觀漂亮。功能比較多！, 螢幕顯示效果不夠細膩；鈴聲效果一般，內建圖片和鈴聲偏少...  
5   [優點很多大家都說了我就不多說了, 一點都不好笑很失望內容也不是很實用, 內容太簡單了，都是...  
6   [雖說費了九牛二虎之力才把系統裝上，感覺用著不錯，速度很快，散熱還好，螢幕完美屏，色彩顯示不...  
7                              [蒙牛，牛逼！, 蒙牛，牛逼, 蒙牛牛逼！]  
8   [月日的訂單，到今天（日）還沒到貨！, 真是讓人鬱悶，噹噹的速度真是慢的讓人崩潰，月日發貨到...  
9   [東西不錯，很好用，安裝師傅服務也很到位，很熱心，贊一個！, 沒有安裝，使用。, 還沒有安裝...  
10  [此款機型硬碟除了服務分割槽外只有一個主分割槽，系列可以考慮出廠預裝系統時做好分割槽, 分割...  
11  [這本書真的很好我向很多朋友介紹了這本書讓人受益非淺, 錯了不是這本書是另外一本真是抱歉不是...  
12  [作業系統啊真不好加一個又用不了多少錢？建議增加安裝系統的服務, 用起來不習慣，速度慢，分割...  
13  [我也喜歡蒙牛的牛奶, 酸奶喝來喝去，還是最喜歡蒙牛的紅棗酸奶，味道香，還便宜, 其實吧。。...  
14  [機子質量不怎麼樣，電話本和簡訊的容量比較小，售後不熱情，待機時間比較短！, 電話或簡訊儲存...  
15  [記憶體比較小了。以後要是裝的話需要加裝一根的記憶體。。, 鍵盤手感不太好。就一個記憶體插槽...

### Inspect documnets of each topic

In [27]:
doc_info = topic_model.get_document_info(docs)
doc_info.query("Topic==1")

Document  Topic            Name  \
21             訊號差得要命。軟體容易出問題。動不動就死。說不完。電池不好。      1  1_電池_小時_電池續_耐用   
27     螢幕轉軸有點鬆，不知道是不是個例電池使用時間實在是一般在網上找不到讀卡器驅動      1  1_電池_小時_電池續_耐用   
152         外形小巧，白色很精緻。功能齊全，無線，藍芽，硬碟，電池續航時間長。      1  1_電池_小時_電池續_耐用   
260    不錯的。非常方便，可以拿到國家圖書館查查資料。電池續航時間非常長，個多小時。      1  1_電池_小時_電池續_耐用   
267                        價效比高，電池厲害，速度快，軟體豐富      1  1_電池_小時_電池續_耐用   
...                                       ...    ...             ...   
6252           電池好，螢幕好漂亮實測上網、聊天的話可以堅持個半小時，還不錯      1  1_電池_小時_電池續_耐用   
6271       螢幕很亮，鍵盤也還挺舒服的，感覺不出特別小，電池好像可以撐個小時左右      1  1_電池_小時_電池續_耐用   
6277   便宜好用，經濟實惠，剛開始待機時間超長，可能和有專門的電源管理模式軟體有關。      1  1_電池_小時_電池續_耐用   
6304             電池是芯的雞肋不是芯的也就罷了芯的總該算標準配置吧不厚道      1  1_電池_小時_電池續_耐用   
6330  螢幕不錯，怕麻煩直接裝了系統，用著還不錯！電池小時左右，有幾種節電模式可以選！      1  1_電池_小時_電池續_耐用   

                                 Representation  \
21    [電池, 小時, 電池續, 耐用, 機時間, 時間, 航時間, 短, 能力, 長]   
27    [電池, 小時, 電池續, 耐用, 機時間, 時間, 航時間, 短, 能力, 長]   
152   [電池, 小時, 電池續, 耐用, 機時間, 時間, 航時間, 短, 能力, 長]   
260   [電池, 小時, 電池續, 耐用, 機時間, 時間, 航時間, 短, 能力, 長]   
267   [電池, 小時, 電池續, 耐用, 機時間, 時間, 航時間, 短, 能力, 長]   
...                                         ...   
6252  [電池, 小時, 電池續, 耐用, 機時間, 時間, 航時間, 短, 能力, 長]   
6271  [電池, 小時, 電池續, 耐用, 機時間, 時間, 航時間, 短, 能力, 長]   
6277  [電池, 小時, 電池續, 耐用, 機時間, 時間, 航時間, 短, 能力, 長]   
6304  [電池, 小時, 電池續, 耐用, 機時間, 時間, 航時間, 短, 能力, 長]   
6330  [電池, 小時, 電池續, 耐用, 機時間, 時間, 航時間, 短, 能力, 長]   

                                    Representative_Docs  \
21    [電池待機時間長，機身小巧，功能比較實用, 電池待機時間長，機身小巧時尚, 外觀漂亮，電池很...   
27    [電池待機時間長，機身小巧，功能比較實用, 電池待機時間長，機身小巧時尚, 外觀漂亮，電池很...   
152   [電池待機時間長，機身小巧，功能比較實用, 電池待機時間長，機身小巧時尚, 外觀漂亮，電池很...   
260   [電池待機時間長，機身小巧，功能比較實用, 電池待機時間長，機身小巧時尚, 外觀漂亮，電池很...   
267   [電池待機時間長，機身小巧，功能比較實用, 電池待機時間長，機身小巧時尚, 外觀漂亮，電池很...   
...                                                 ...   
6252  [電池待機時間長，機身小巧，功能比較實用, 電池待機時間長，機身小巧時尚, 外觀漂亮，電池很...   
6271  [電池待機時間長，機身小巧，功能比較實用, 電池待機時間長，機身小巧時尚, 外觀漂亮，電池很...   
6277  [電池待機時間長，機身小巧，功能比較實用, 電池待機時間長，機身小巧時尚, 外觀漂亮，電池很...   
6304  [電池待機時間長，機身小巧，功能比較實用, 電池待機時間長，機身小巧時尚, 外觀漂亮，電池很...   
6330  [電池待機時間長，機身小巧，功能比較實用, 電池待機時間長，機身小巧時尚, 外觀漂亮，電池很...   

                                           Top_n_words  Probability  \
21    電池 - 小時 - 電池續 - 耐用 - 機時間 - 時間 - 航時間 - 短 - 能力 - 長       0.2613   
27    電池 - 小時 - 電池續 - 耐用 - 機時間 - 時間 - 航時間 - 短 - 能力 - 長       0.1653   
152   電池 - 小時 - 電池續 - 耐用 - 機時間 - 時間 - 航時間 - 短 - 能力 - 長       0.3567   
260   電池 - 小時 - 電池續 - 耐用 - 機時間 - 時間 - 航時間 - 短 - 能力 - 長       0.3012   
267   電池 - 小時 - 電池續 - 耐用 - 機時間 - 時間 - 航時間 - 短 - 能力 - 長       0.2374   
...                                                ...          ...   
6252  電池 - 小時 - 電池續 - 耐用 - 機時間 - 時間 - 航時間 - 短 - 能力 - 長       0.1888   
6271  電池 - 小時 - 電池續 - 耐用 - 機時間 - 時間 - 航時間 - 短 - 能力 - 長       0.1979   
6277  電池 - 小時 - 電池續 - 耐用 - 機時間 - 時間 - 航時間 - 短 - 能力 - 長       0.0848   
6304  電池 - 小時 - 電池續 - 耐用 - 機時間 - 時間 - 航時間 - 短 - 能力 - 長       0.5785   
6330  電池 - 小時 - 電池續 - 耐用 - 機時間 - 時間 - 航時間 - 短 - 能力 - 長       0.0990   

      Representative_document  
21                      False  
27                      False  
152                     False  
260                     False  
267                     False  
...                       ...  
6252                    False  
6271                    False  
6277                    False  
6304                    False  
6330                    False  

[160 rows x 8 columns]

### Topic-terms overview of all topics

In [28]:
all_topics = topic_model.get_topics()
df_all_topics = pd.DataFrame(all_topics)
df_all_topics

-1                           0   \
0  (蒙牛, 0.012909055419502172)   (酒店, 0.03997580428200383)   
1   ( , 0.010304950123438766)  (房間, 0.038745198337690454)   
2   (買, 0.008769904965208518)   (住, 0.022947505352807967)   
3   (喝, 0.008295668253548046)  (服務, 0.021592129521251717)   
4  (不錯, 0.007054007264300265)   (環境, 0.02153355858267068)   
5   (書, 0.006872649797849081)  (早餐, 0.020479389742980674)   
6  (外觀, 0.006786229328450595)  (設施, 0.020377022207918306)   
7   (好, 0.006520041858347239)  (入住, 0.017575327768934505)   
8  (支援, 0.006246563289206007)  (方便, 0.015658263760673603)   
9   (說, 0.005924667413511004)  (交通, 0.015161822535778819)   

                            1                           2   \
0    (電池, 0.10812010727779262)   (鍵盤, 0.09556198048611775)   
1    (小時, 0.03984937954514461)  (手感, 0.047830507131678635)   
2  (電池續, 0.035890356214032144)  (舒服, 0.027319204208813903)   
3   (耐用, 0.023812950945556306)  (按鍵, 0.019931836455130924)   
4  (機時間, 0.023096786477421298)   (鍵, 0.019332443408215924)   
5    (時間, 0.02285988070535654)   (螢幕, 0.01670485474907205)   
6  (航時間, 0.022430461802901747)   (好, 0.015471207546496252)   
7    (短, 0.020217140990209503)  (價效, 0.014554356827744926)   
8    (能力, 0.02013993549795948)  (外觀, 0.013659179514628934)   
9     (長, 0.01995175249529089)   (盤, 0.012682195897824317)   

                           3                           4   \
0   (鈴聲, 0.05432354411091842)   (內容, 0.04941998010576315)   
1   (聲音, 0.04106639099316521)   (說, 0.037074906367358676)   
2    (效果, 0.0401551840731225)   (失望, 0.03257476908734506)   
3  (音質, 0.037809712251507026)  (優點, 0.025207720385531977)   
4   (功能, 0.03189185647319983)  (覺得, 0.024410570339298696)   
5   (聽, 0.027846290729857216)     (人, 0.0219268791461538)   
6   (螢幕, 0.02661743013461871)   (感覺, 0.02090861601908716)   
7  (音量, 0.022135759224421948)  (暢銷, 0.019759176884332354)   
8   (顯示, 0.02167928726545306)  (宣傳, 0.018008594527023355)   
9  (拍照, 0.020016906486091956)  (好看, 0.017409958362111826)   

                           5                           6   \
0   (螢幕, 0.07327764549880973)   (蒙牛, 0.09746961535036144)   
1   (屏, 0.028146483478746955)    (逼, 0.06656569965699044)   
2  (顯示, 0.026441819533747322)    (牛, 0.06432426930409332)   
3  (完美, 0.025704439878893197)  (抵制, 0.059442883742549545)   
4  (亮點, 0.023289275436560897)    (真, 0.04093362592078666)   
5  (效果, 0.022558883729691365)   (悲劇, 0.04023492974101406)   
6   (外觀, 0.01993637101120427)    (傻, 0.03966353099568117)   
7  (功能, 0.017064884459850917)   (可怕, 0.03562739263571287)   
8  (色彩, 0.017049676086780086)     ( , 0.0275336479021026)   
9   (配置, 0.01472443214030595)  (垃圾, 0.027003363852405215)   

                          7                            8   ...  \
0  (收到, 0.06910198665903361)    (安裝, 0.08700249495130657)  ...   
1   (月, 0.05407443598159331)    (師傅, 0.06008049613116295)  ...   
2   (日, 0.04271689794271339)  (還沒安裝, 0.05156862237250838)  ...   
3  (訂單, 0.04271689794271339)   (安裝費, 0.04237693574593841)  ...   
4  (還沒, 0.03452525938917517)    (東西, 0.03731307583454291)  ...   
5  (書, 0.034397328244441354)     (再, 0.02817535305805783)  ...   
6  (噹噹, 0.03352139356408797)     (好, 0.02723021895285468)  ...   
7  (通知, 0.03288682397142727)   (正品, 0.024886767779991912)  ...   
8  (缺貨, 0.03157323019629331)   (先給, 0.024211421249839108)  ...   
9  (沒貨, 0.03157323019629331)    (好評, 0.02369382457538249)  ...   

                           82                          83  \
0    (上網, 0.1805240316283576)   (支援, 0.28485833794752696)   
1   (太麻煩, 0.0904118022924759)   (贊助, 0.24187349561088978)   
2   (連線, 0.08663081788262814)  (一如既往, 0.1612489970739265)   
3   (網路, 0.07944077562404209)   (實力, 0.11758556057831634)   
4    (線, 0.07610450044555302)  (湯之贇, 0.11758556057831634)   
5  (網絡卡, 0.07324697651104445)   (我算, 0.11758556057831634)   
6   (臥室, 0.06931359360406017)   (湯湯, 0.11758556057831634)   
7  (說產品, 0.06931359360406017)    (噠, 0.11758556057831634)   
8   (老好, 0.06931359360406017)   (出國, 0.117585560578

### LDAVis (Relation between topics)

In [32]:
topic_model.visualize_topics()

ValueError: Mime type rendering requires nbformat>=4.2.0 but it is not installed

Figure({
    'data': [{'customdata': array([[0, '酒店 | 房間 | 住 | 服務 | 環境', 842],
                                   [1, '電池 | 小時 | 電池續 | 耐用 | 機時間', 160],
                                   [2, '鍵盤 | 手感 | 舒服 | 按鍵 | 鍵', 148],
                                   ...,
                                   [89, '半年 | 月 | 兩天 | 沒死 | 用天', 10],
                                   [90, '綠色 | 心情 | 笑 | 悲春傷 | 秋', 10],
                                   [91, '時尚 | 功能 | 外型 | 強大質量 | 夠輕薄', 10]], dtype=object),
              'hovertemplate': '<b>Topic %{customdata[0]}</b><br>%{customdata[1]}<br>Size: %{customdata[2]}',
              'legendgroup': '',
              'marker': {'color': '#B0BEC5',
                         'line': {'color': 'DarkSlateGrey', 'width': 2},
                         'size': array([842, 160, 148, 133, 119, 119, 118,  98,  98,  87,  85,  85,  84,  77,
                                         77,  72,  72,  64,  61,  61,  57,  55,  51,  50,  50,  50,  43,  43,
                                         42,  41,  40,  36,  36,  35,  34,  34,  32,  29,  28,  28,  27,  26,
                                         26,  25,  25,  25,  25,  24,  24,  23,  23,  23,  22,  22,  21,  21,
                                         21,  21,  19,  19,  19,  18,  17,  17,  17,  17,  16,  16,  16,  15,
                                         15,  15,  15,  15,  14,  14,  13,  13,  13,  13,  13,  12,  12,  12,
                                         11,  11,  11,  11,  11,  10,  10,  10]),
                         'sizemode': 'area',
                         'sizeref': 0.52625,
                         'symbol': 'circle'},
              'mode': 'markers',
              'name': '',
              'orientation': 'v',
              'showlegend': False,
              'type': 'scatter',
              'x': array([  2.0618346 ,  -4.177035  ,  -4.0967607 , -10.415916  ,  -2.8295069 ,
                           -4.0974274 ,  14.198157  ,   7.869223  ,  -1.1193897 , -10.390404  ,
                            6.8532476 ,  -1.1418871 ,   5.1356196 ,   2.6757567 , -10.337044  ,
                           -1.2306204 ,  -7.4664497 ,   8.86541   ,  -7.5065646 ,   5.1827974 ,
                           -4.297485  ,   2.4566667 ,   6.780926  ,   3.36425   ,   2.0869627 ,
                           19.511795  ,   5.202037  ,  -1.4096951 ,  -4.0474834 ,  -3.9821832 ,
                           -0.35340914,   7.986873  ,   7.3561716 ,   4.7203045 ,   6.86245   ,
                            2.1439204 ,  -4.2116766 ,   2.5149121 ,  -7.658988  ,   2.0094523 ,
                            8.950322  ,   4.517659  ,   7.53809   ,   4.56207   , -11.930233  ,
                           19.512632  ,   2.3537316 , -11.930255  , -12.83634   , -12.8363495 ,
                           15.317791  ,  -2.733032  ,  -1.4371524 , -10.515718  ,   3.3346875 ,
                            5.031971  ,   8.391907  ,  -2.718663  , -10.345059  ,  15.317891  ,
                           -0.28825098,   7.9044623 ,   7.3238363 ,   2.5547225 ,   7.2912173 ,
                            8.5589285 ,   8.227265  ,   3.3709478 ,  -0.4811564 ,   8.35838   ,
                           -0.6404449 ,   6.745173  ,  13.890411  ,   7.4027395 ,   4.6999516 ,
                          -10.598011  ,   5.0200095 ,  -0.585409  ,  14.239146  ,  -0.5847238 ,
                            8.498008  ,   8.490253  ,   2.795004  ,  14.352147  ,  -4.163009  ,
                           14.230393  ,  -1.3673314 ,   6.7022433 ,  -7.552661  ,  -0.60941654,
                           13.973764  ,   4.5799537 ], dtype=float32),
              'xaxis': 'x',
              'y': array([ 7.553768  , -0.92157286, -0.72885484, -5.5102477 ,  5.9137297 ,
                          -0.24692878,  6.3341236 , -6.659408  , -0.98779047, -5.1393085 ,
                           4.5546627 , -0.9635181 , 16.251976  ,  8.868409  , -5.0250177 ,
                          -0.8753445 , -6.261693  , 11.0668125 , -6.3045845 , 16.56741   ,
                 

### Topic-term bar-charts

In [33]:
topic_model.visualize_barchart(top_n_topics=10, n_words = 10, topics = range(10))

ValueError: Mime type rendering requires nbformat>=4.2.0 but it is not installed

Figure({
    'data': [{'marker': {'color': '#D55E00'},
              'orientation': 'h',
              'type': 'bar',
              'x': [0.015161822535778819, 0.015658263760673603,
                    0.017575327768934505, 0.020377022207918306,
                    0.020479389742980674, 0.02153355858267068,
                    0.021592129521251717, 0.022947505352807967,
                    0.038745198337690454, 0.03997580428200383],
              'xaxis': 'x',
              'y': [交通  , 方便  , 入住  , 設施  , 早餐  , 環境  , 服務  , 住  , 房間  , 酒店  ],
              'yaxis': 'y'},
             {'marker': {'color': '#0072B2'},
              'orientation': 'h',
              'type': 'bar',
              'x': [0.01995175249529089, 0.02013993549795948,
                    0.020217140990209503, 0.022430461802901747,
                    0.02285988070535654, 0.023096786477421298,
                    0.023812950945556306, 0.035890356214032144,
                    0.03984937954514461, 0.10812010727779262],
              'xaxis': 'x2',
              'y': [長  , 能力  , 短  , 航時間  , 時間  , 機時間  , 耐用  , 電池續  , 小時  , 電池  ],
              'yaxis': 'y2'},
             {'marker': {'color': '#CC79A7'},
              'orientation': 'h',
              'type': 'bar',
              'x': [0.012682195897824317, 0.013659179514628934,
                    0.014554356827744926, 0.015471207546496252,
                    0.01670485474907205, 0.019332443408215924,
                    0.019931836455130924, 0.027319204208813903,
                    0.047830507131678635, 0.09556198048611775],
              'xaxis': 'x3',
              'y': [盤  , 外觀  , 價效  , 好  , 螢幕  , 鍵  , 按鍵  , 舒服  , 手感  , 鍵盤  ],
              'yaxis': 'y3'},
             {'marker': {'color': '#E69F00'},
              'orientation': 'h',
              'type': 'bar',
              'x': [0.020016906486091956, 0.02167928726545306,
                    0.022135759224421948, 0.02661743013461871,
                    0.027846290729857216, 0.03189185647319983,
                    0.037809712251507026, 0.0401551840731225, 0.04106639099316521,
                    0.05432354411091842],
              'xaxis': 'x4',
              'y': [拍照  , 顯示  , 音量  , 螢幕  , 聽  , 功能  , 音質  , 效果  , 聲音  , 鈴聲  ],
              'yaxis': 'y4'},
             {'marker': {'color': '#56B4E9'},
              'orientation': 'h',
              'type': 'bar',
              'x': [0.017409958362111826, 0.018008594527023355,
                    0.019759176884332354, 0.02090861601908716, 0.0219268791461538,
                    0.024410570339298696, 0.025207720385531977,
                    0.03257476908734506, 0.037074906367358676, 0.04941998010576315],
              'xaxis': 'x5',
              'y': [好看  , 宣傳  , 暢銷  , 感覺  , 人  , 覺得  , 優點  , 失望  , 說  , 內容  ],
              'yaxis': 'y5'},
             {'marker': {'color': '#009E73'},
              'orientation': 'h',
              'type': 'bar',
              'x': [0.01472443214030595, 0.017049676086780086,
                    0.017064884459850917, 0.01993637101120427,
                    0.022558883729691365, 0.023289275436560897,
                    0.025704439878893197, 0.026441819533747322,
                    0.028146483478746955, 0.07327764549880973],
              'xaxis': 'x6',
              'y': [配置  , 色彩  , 功能  , 外觀  , 效果  , 亮點  , 完美  , 顯示  , 屏  , 螢幕  ],
              'yaxis': 'y6'},
             {'marker': {'color': '#F0E442'},
              'orientation': 'h',
              'type': 'bar',
              'x': [0.027003363852405215, 0.0275336479021026, 0.03562739263571287,
                    0.03966353099568117, 0.04023492974101406, 0.04093362592078666,
                    0.059442883742549545, 0.06432426930409332, 0.06656569965699044,
                    0.09746961535036144],
              'xaxis': 'x7',
              'y': [垃圾  ,    , 可怕  , 傻  , 悲劇  , 真  , 抵制  , 牛  , 逼  , 蒙牛  ],
              'yaxis': 'y7'},
             {'marker': {'color': '#D55E00'},
              'orientation': 'h',
        

### Document distribution with topics

In [34]:
topic_model.visualize_documents(docs, hide_document_hover = True, topics=range(16))

ValueError: Mime type rendering requires nbformat>=4.2.0 but it is not installed

Figure({
    'data': [{'hoverinfo': 'text',
              'marker': {'color': '#CFD8DC', 'opacity': 0.5, 'size': 5},
              'mode': 'markers+text',
              'name': 'other',
              'showlegend': False,
              'type': 'scattergl',
              'x': array([-0.73092115, -0.7264726 , -0.7414604 , ...,  2.116739  , -3.091785  ,
                          -0.68408906], dtype=float32),
              'y': array([ 2.3918753 ,  2.419845  ,  2.3724346 , ..., -0.96752244, -0.59807104,
                          -0.80916363], dtype=float32)},
             {'hoverinfo': 'text',
              'marker': {'opacity': 0.5, 'size': 5},
              'mode': 'markers+text',
              'name': '0_酒店_房間_住',
              'text': array(['', '', '', ..., '', '', '0_酒店_房間_住'], dtype=object),
              'textfont': {'size': 12},
              'type': 'scattergl',
              'x': array([-1.6095887, -1.98206  , -1.1330969, ..., -1.0013577, -1.2558184,
                          -1.188734 ], dtype=float32),
              'y': array([10.709421 , 10.542359 , 10.03907  , ..., 10.3191595,  9.745701 ,
                          10.284611 ], dtype=float32)},
             {'hoverinfo': 'text',
              'marker': {'opacity': 0.5, 'size': 5},
              'mode': 'markers+text',
              'name': '1_電池_小時_電池續',
              'text': array(['', '', '', '', '', '', '', '', '', '', '', '', '', '', '', '', '', '',
                             '', '', '', '', '', '', '', '', '', '', '', '', '', '', '', '', '', '',
                             '', '', '', '', '', '', '', '', '', '', '', '', '', '', '', '', '', '',
                             '', '', '', '', '', '', '', '', '', '', '', '', '', '', '', '', '', '',
                             '', '', '', '', '', '', '', '', '', '', '', '', '', '', '', '', '', '',
                             '', '', '', '', '', '', '', '', '', '', '', '', '', '', '', '', '', '',
                             '', '', '', '', '', '', '', '', '', '', '', '', '', '', '', '', '', '',
                             '', '', '', '', '', '', '', '', '', '', '', '', '', '', '', '', '', '',
                             '', '', '', '', '', '', '', '', '', '', '', '', '', '', '', '',
                             '1_電池_小時_電池續'], dtype=object),
              'textfont': {'size': 12},
              'type': 'scattergl',
              'x': array([-5.2262387, -5.769334 , -5.6280203, -5.2111235, -5.5289817, -5.6454873,
                          -5.3612704, -5.4598007, -5.522536 , -5.370318 , -5.7178907, -5.5586185,
                          -5.7793508, -5.025257 , -5.483622 , -5.7719855, -5.6743484, -5.469044 ,
                          -5.610182 , -5.7613053, -5.5443277, -5.7741547, -5.3639007, -5.6614356,
                          -5.7204404, -5.3838387, -5.655655 , -5.4633746, -5.447223 , -5.3735147,
                          -5.582442 , -5.219029 , -4.9643326, -5.627865 , -5.285899 , -5.550124 ,
                          -5.5047154, -5.307671 , -5.6037064, -5.7285304, -5.0881147, -5.37308  ,
                          -5.586427 , -5.7098413, -5.351071 , -5.6330557, -5.431394 , -5.214593 ,
                          -5.554505 , -5.51913  , -5.991678 , -5.732512 , -5.169172 , -5.378438 ,
                          -5.037686 , -5.4025807, -5.3002844, -5.730987 , -5.5601006, -5.356227 ,
                          -5.0956683, -5.5731535, -5.4558764, -5.6011276, -5.5166717, -5.247009 ,
                          -5.555326 , -5.4787006, -5.0092463, -5.734115 , -5.3756375, -5.605139 ,
                          -5.505066 , -5.3502936, -5.4708123, -5.130663 , -5.2591887, -5.6983275,
                          -5.6636252, -5.561783 , -5.3786716, -5.6244493, -5.221061 , -5.600943 ,
                          -5.662549 , -5.712276 , -5.0351696, -5.344728 , -5.4460096, -5.5092454,
                          -5.2544246, -5.141017 , -5.39614  , -5.5731153, -5.313584 , -5.4404426,
                          -5.3198156, -5.3593388, -5.145264 